In [1]:
# # Experiment Settings, logger, plotter
# from utils.exp_logger import Logger
# from utils.exp_metrics_plotter import MetricsPlotter
# from utils.utils import set_settings
# from utils.exp_config import get_config

# config = get_config("OurModelConfig")
# set_settings(config)
bs = 32

In [2]:
from collections import defaultdict
import os
import onnx
import time
import torch
import random
import numpy as np
from torch_geometric.data import Data, Dataset
from feature.graph_feature import extract_graph_feature

import numpy as np
import networkx as nx
from feature.onnx_to_networkx import onnx2nx
from feature.onnx_shape_infer import custom_shape_infer
from feature.onnx_flops import calculate_onnx_flops
from feature.node_feature import extract_node_features


def modify_onnx_batch_size(onnx_G, batch_size):
    # initializer names, in case of names of input include initializers
    init_names = set()
    for init in onnx_G.graph.initializer:
        init_names.add(init.name)

    def _modify(node, dim_idx, value):
        dims = node.type.tensor_type.shape.dim
        if len(dims) > dim_idx:
            value = value[node.name] if isinstance(value, dict) else value
            dims[dim_idx].dim_value = value

    # modify input
    for inp in onnx_G.graph.input:
        if inp.name in init_names:
            continue
        _modify(inp, 0, batch_size)

    # modify output
    for out in onnx_G.graph.output:
        _modify(out, 0, batch_size)

    return


def parse_from_onnx(onnx_path, batch_size):
    pG = onnx2nx(onnx_path)
    nx_G, onnx_G = pG.data, pG.onnx_G

    # first we should change the batch_size of input in ONNX model
    modify_onnx_batch_size(onnx_G, batch_size)
    status, newG, output_shapes = custom_shape_infer(onnx_G)
    # if failed modify the batch to original batch size
    assert status is True, "Onnx shape infer error!"

    flops, params, macs, node_flops = calculate_onnx_flops(onnx_G, True)
    return nx_G, output_shapes, flops, params, macs, node_flops, newG


def extract_graph_feature_from_networkx(nx_G, batch_size, output_shapes, flops, params, macs, undirected=True):
    # static features: flops, params, memory_access (GB) + batch_size
    static_features = np.array([batch_size, flops / 1e9, params / 1e9, macs / 1e9], dtype="float32")

    # node features
    node_features = extract_node_features(nx_G, output_shapes, batch_size)

    # get features conducted by idx
    features = []
    name2id = {}
    id2name = {}
    for idx, node in enumerate(nx.topological_sort(nx_G)):
        features.append(node_features[node])
        name2id[node] = idx
        id2name[idx] = node

    # get graph adjacent matrix
    node_num = nx_G.number_of_nodes()
    adjacent = np.zeros((node_num, node_num), dtype="float32")

    for node in nx_G.nodes():
        idx = name2id[node]
        for child in nx_G.successors(node):
            conn_idx = name2id[child]
            adjacent[idx][conn_idx] = 1
            if undirected:
                adjacent[conn_idx][idx] = 1

    # test connect relationship
    # xs, ys = np.where(adjacent > 0)
    # for i in range(len(xs)):
    #     print("Conn:", id2name[xs[i]], id2name[ys[i]])

    # feature in features may be a tuple (block_adjacent, block_features, block_static_features)
    return adjacent, features, static_features


def extract_graph_feature(onnx_path, batch_size, return_onnx=False):
    nx_G, output_shapes, flops, params, macs, node_flops, onnx_G = parse_from_onnx(onnx_path, batch_size)
    
    adjacent, features, static_features = extract_graph_feature_from_networkx(
        nx_G, batch_size, output_shapes, flops, params, macs
    )

    if return_onnx:
        return adjacent, np.array(features), static_features, onnx_G
    else:
        return adjacent, np.array(features), static_features

def get_torch_data(onnx_file, batch_size, cost_time):
    adjacent, node_features, static_features = extract_graph_feature(onnx_file, batch_size)
    # print(adjacent)
    edge_index = torch.from_numpy(np.array(np.where(adjacent > 0))).type(torch.long)
    node_features = np.array(node_features, dtype=np.float32)
    x = torch.from_numpy(node_features).type(torch.float)
    sf = torch.from_numpy(static_features).type(torch.float)
    y = torch.FloatTensor([cost_time])
    data = Data(
        x = x,
        edge_index = edge_index,
        y = y,
    )
    # 2025年12月16日20:35:31 在这里添加我想要的内容
    # data = {
    #     "key": [],
    #     "adj_matrix": [],
    #     "features": [],
    #     "flops": [],
    #     "params": [],
    #     "accuracy": [],
    #     "latency": [],
    # }
    return data, sf


class GraphLatencyDataset(Dataset):
    # specific a platform
    def __init__(self, root, onnx_dir, latency_file, override_data=False, transform=None, pre_transform=None,
                model_types=None, train_test_stage=None, indomains=False, platforms=None, sample_num=-1):
        super(GraphLatencyDataset, self).__init__(root, transform, pre_transform)
        self.onnx_dir = onnx_dir
        self.latency_file = latency_file
        self.latency_ids = []
        self.override_data = override_data
        self.model_types = model_types
        self.train_test_stage = train_test_stage
        self.platforms = platforms

        # 2025年12月16日19:59:05，来给indomain问题添加一个验证测试的特判取数据
        self.indomains = indomains
        
        # Load the gnn model for block
        self.device = None
        print("Extract input data from onnx...")
        self.custom_process()
        print("Done.")

        if sample_num > 0:
            random.seed(1234)
            random.shuffle(self.latency_ids)
            self.latency_ids = self.latency_ids[:sample_num]
        random.seed(1234)
        random.shuffle(self.latency_ids)

    @property
    def raw_file_names(self):
        return []

    @property
    def processed_file_names(self):
        return []

    def download(self):
        pass

    def process(self):
        pass

    def custom_process(self):
        # 1. 初始化一个计数器，用来记录每个模型出现了多少次
        model_counter = defaultdict(int)
        with open(self.latency_file) as f:
            for line in f.readlines():

                line = line.rstrip()
                items = line.split(" ")
                speed_id = str(items[0])
                graph_id = str(items[1])
                batch_size = int(items[2])
                cost_time = float(items[3])
                plt_id = int(items[5])
                

                if self.model_types and items[4] not in self.model_types:
                    continue

                if self.platforms and plt_id not in self.platforms:
                    continue

                if self.train_test_stage and items[6] != self.train_test_stage:
                    continue
                    
                # 3. 增加计数
                model_type = items[4]  # 提取模型类型
                model_counter[model_type] += 1
                current_count = model_counter[model_type]
                
                if self.indomains == 'train':
                    # 训练集：只要前 1800 个，超过的跳过
                    if current_count > 1800:
                        continue
                        
                        
                elif self.indomains == 'test':
                    # 测试集：只要 1800 之后的 (即最后 10%)
                    if current_count <= 1800:
                        continue

                onnx_file = os.path.join(self.onnx_dir, graph_id)
                if os.path.exists(onnx_file):
                    data_file = os.path.join(self.processed_dir, '{}_{}_data.pt'.format(speed_id, plt_id))
                    sf_file = os.path.join(self.processed_dir, '{}_{}_sf.pt'.format(speed_id, plt_id))
                    graph_name = "{}_{}_{}".format(graph_id, batch_size, plt_id)
                    self.latency_ids.append((data_file, sf_file, graph_name, plt_id))

                    if (not self.override_data) and os.path.exists(data_file) and os.path.exists(sf_file):
                        continue

                    if len(self.latency_ids) % 1000 == 0:
                        print(len(self.latency_ids))

                    try:
                        GG = onnx.load(onnx_file)
                        data, sf = get_torch_data(GG, batch_size, cost_time)

                        if self.pre_filter is not None and not self.pre_filter(data):
                            continue
                        if self.pre_transform is not None:
                            data = self.pre_transform(data)

                        torch.save(data, data_file)
                        torch.save(sf, sf_file)
                    except Exception as e:
                        self.latency_ids.pop()
                        print("Error", e)

    def len(self):
        return len(self.latency_ids)

    def get(self, idx):
        data_file, sf_file, graph_name, plt_id = self.latency_ids[idx]
        data = torch.load(data_file)
        sf = torch.load(sf_file)
        return data, sf, graph_name, plt_id

/opt/anaconda3/envs/latency/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [3]:
"""
    俩个场景
    1、Out of domain latency prediction on NNLQ
    2、In domain latency prediction on NNLQ
"""

'\n    俩个场景\n    1、Out of domain latency prediction on NNLQ\n    2、In domain latency prediction on NNLQ\n'

In [8]:
data_root = '../data/nnlqp/unseen_structure'
all_latency_file = data_root + "/gt.txt"
onnx_dir = data_root
all_scnarios = ['resnet18', 'vgg16', 'efficientb0', 'mobilenetv2', 'mobilenetv3', 'mnasnet', 'alexnet', 'squeezenet', 'googlenet', 'nasbench201']
override_data = False
multi_plt = None

In [9]:
# 这里是Out of the domain Testing 
from torch.utils.data import DataLoader
for test_model_type in all_scnarios:
    model_types = set()
    for line in open(all_latency_file).readlines():
        model_types.add(line.split()[4])
    test_model_types = set([test_model_type])
    # if train_model_types:
        # train_model_types = set(train_model_types.split(','))
        # train_model_types = train_model_types & model_types
    # else:
    train_model_types = model_types - test_model_types
    assert len(train_model_types) > 0
    # allow_platforms=config.multi_plt.keys() if config.multi_plt else None
    allow_platforms=None

    print("Train model types: {}".format(train_model_types))
    print("Test model types: {}".format(test_model_types))
    print("Platforms: {}".format(allow_platforms))

    train_set = GraphLatencyDataset(
        data_root,
        onnx_dir,
        all_latency_file,
        override_data=override_data,
        model_types=train_model_types,
        platforms=allow_platforms,
    )
    test_set = GraphLatencyDataset(
        data_root,
        onnx_dir,
        all_latency_file,
        override_data=override_data,
        model_types=test_model_types,
        platforms=allow_platforms,
    )

    print("Train data = {}, Test data = {}".format(len(train_set), len(test_set)))
    train_loader = DataLoader(dataset=train_set, batch_size=bs, shuffle=True)
    test_loader = DataLoader(dataset=test_set, batch_size=bs, shuffle=False)

Train model types: {'mobilenetv3', 'squeezenet', 'mnasnet', 'alexnet', 'vgg16', 'efficientb0', 'googlenet', 'mobilenetv2', 'nasbench201'}
Test model types: {'resnet18'}
Platforms: None
Extract input data from onnx...
 - Warning: onnx version should in ['1.7.0', '1.8.1'], but with 1.18.0, infer shape may cause error
 - Warning: onnx version should in ['1.7.0', '1.8.1'], but with 1.18.0, infer shape may cause error
 - Warning: onnx version should in ['1.7.0', '1.8.1'], but with 1.18.0, infer shape may cause error
 - Warning: onnx version should in ['1.7.0', '1.8.1'], but with 1.18.0, infer shape may cause error
 - Warning: onnx version should in ['1.7.0', '1.8.1'], but with 1.18.0, infer shape may cause error
 - Warning: onnx version should in ['1.7.0', '1.8.1'], but with 1.18.0, infer shape may cause error
 - Warning: onnx version should in ['1.7.0', '1.8.1'], but with 1.18.0, infer shape may cause error
 - Warning: onnx version should in ['1.7.0', '1.8.1'], but with 1.18.0, infer shape

Processing...
Done!


 - Warning: onnx version should in ['1.7.0', '1.8.1'], but with 1.18.0, infer shape may cause error
 - Warning: onnx version should in ['1.7.0', '1.8.1'], but with 1.18.0, infer shape may cause error
 - Warning: onnx version should in ['1.7.0', '1.8.1'], but with 1.18.0, infer shape may cause error
 - Warning: onnx version should in ['1.7.0', '1.8.1'], but with 1.18.0, infer shape may cause error
 - Warning: onnx version should in ['1.7.0', '1.8.1'], but with 1.18.0, infer shape may cause error
 - Warning: onnx version should in ['1.7.0', '1.8.1'], but with 1.18.0, infer shape may cause error
 - Warning: onnx version should in ['1.7.0', '1.8.1'], but with 1.18.0, infer shape may cause error
 - Warning: onnx version should in ['1.7.0', '1.8.1'], but with 1.18.0, infer shape may cause error
 - Warning: onnx version should in ['1.7.0', '1.8.1'], but with 1.18.0, infer shape may cause error
 - Warning: onnx version should in ['1.7.0', '1.8.1'], but with 1.18.0, infer shape may cause error


KeyboardInterrupt: 

In [ ]:
# This is the in of the domain Testing 
# from torch.utils.data import DataLoader
from torch_geometric.loader import DataLoader  # <--- 改用这个
# 注意：在旧版 PyG 中可能是 from torch_geometric.data import DataLoader
model_types = set()
for line in open(all_latency_file).readlines():
    model_types.add(line.split()[4])
test_model_types = set([test_model_type])
train_model_types = model_types
assert len(train_model_types) > 0
allow_platforms=None

print("Train model types: {}".format(train_model_types))

/opt/anaconda3/envs/latency/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


NameError: name 'all_latency_file' is not defined

In [ ]:
train_set = GraphLatencyDataset(
    data_root,
    onnx_dir,
    all_latency_file,
    override_data=override_data,
    model_types=train_model_types,
    platforms=allow_platforms,
    indomains='train',
)

test_set = GraphLatencyDataset(
    data_root,
    onnx_dir,
    all_latency_file,
    override_data=override_data,
    model_types=train_model_types,
    platforms=allow_platforms,
    indomains='test',
)

print("Train data = {}, Test data = {}".format(len(train_set), len(test_set)))
train_loader = DataLoader(dataset=train_set, batch_size=bs, shuffle=True)
test_loader = DataLoader(dataset=test_set, batch_size=bs, shuffle=False)

Extract input data from onnx...
Done.


Processing...
Done!
Processing...
Done!


Extract input data from onnx...
Done.
Train data = 16200, Test data = 1800


NameError: name 'bs' is not defined

In [ ]:
for batch in train_loader:
    data, static_feature, _, plt_id = batch
    data.y = data.y.view(-1, 1)
    print(data.x.shape)
    print(static_feature[0])
    print(static_feature[1])
    print(static_feature[2])
    print(static_feature[9])
    # static_feature [bs, flops, parameters, macs]
    break 

torch.Size([25832, 44])
tensor([ 1.0000, 10.0673,  0.0115,  0.0245])
tensor([1.0000, 0.4976, 0.0318, 0.0328])
tensor([1.0000, 0.5021, 0.0504, 0.0517])
tensor([1.0000, 7.5620, 0.0286, 0.0446])


In [10]:
# 制作单个样本，给NNLQP做全部所需要的东西

data = {
    "key": [],
    "adj_matrix": [],
    "features": [],
    "flops": [],
    "params": [],
    "model_type": [],
    "latency": [],
}
latency_file = '../data/nnlqp/unseen_structure/gt.txt'
onnx_dir = '../data/nnlqp/unseen_structure/'

max_length = -1
with open(latency_file) as f:
    for line in f.readlines():
        line = line.rstrip()
        items = line.split(" ")
        speed_id = str(items[0])
        graph_id = str(items[1])
        batch_size = int(items[2])
        plt_id = int(items[5])

        # 这个使我们需要预测的任务
        cost_time = float(items[3])
        # print(cost_time)
        onnx_file = os.path.join(onnx_dir, graph_id)
        
        # 已经读取到了数据，请在这里拿到自己所有想要的东西
        GG = onnx.load(onnx_file)
        adjacent, node_features, static_features = extract_graph_feature(onnx_file, batch_size)
        # sf = [batch size, flops, parameters, macs]
        # print(adjacent.shape, node_features.shape, static_features.shape)
        
        # 我想要的全部东西，都已经拿到了
        adj_matrix = adjacent
        features = node_features[:, :32]
        features = np.argmax(features, axis=1)
        flops = static_features[1] 
        params = static_features[2] 
        latency = cost_time
        
        # -------- 改成往 list 里 append --------
        data["key"].append(graph_id)
        data["adj_matrix"].append(adj_matrix)
        data["features"].append(features)
        data["flops"].append(flops)
        data['model_type'].append(items[4])
        data["params"].append(params)
        data["latency"].append(latency)
        
        max_length = max(max_length, len(adj_matrix))
        # break

Read Onnx: ../data/nnlqp/unseen_structure/onnx/nnmeter_alexnet/nnmeter_alexnet_transform_0000.onnx
 - Warning: onnx version should in ['1.7.0', '1.8.1'], but with 1.18.0, infer shape may cause error
 - Warning: onnx version should in ['1.7.0', '1.8.1'], but with 1.18.0, infer shape may cause error
Read Onnx: ../data/nnlqp/unseen_structure/onnx/nnmeter_alexnet/nnmeter_alexnet_transform_0001.onnx
 - Warning: onnx version should in ['1.7.0', '1.8.1'], but with 1.18.0, infer shape may cause error
 - Warning: onnx version should in ['1.7.0', '1.8.1'], but with 1.18.0, infer shape may cause error
Read Onnx: ../data/nnlqp/unseen_structure/onnx/nnmeter_alexnet/nnmeter_alexnet_transform_0002.onnx
 - Warning: onnx version should in ['1.7.0', '1.8.1'], but with 1.18.0, infer shape may cause error
 - Warning: onnx version should in ['1.7.0', '1.8.1'], but with 1.18.0, infer shape may cause error
Read Onnx: ../data/nnlqp/unseen_structure/onnx/nnmeter_alexnet/nnmeter_alexnet_transform_0003.onnx
 - W

In [11]:
max_length

245

In [12]:
import pickle 

with open('../data/nnlqp_latency_data.pkl', 'wb') as f:
    pickle.dump(data, f)

In [4]:
import pickle 

with open("../data/nnlqp_latency_data.pkl", "rb") as f:
    data = pickle.load(f)


In [5]:
data.keys()

dict_keys(['key', 'adj_matrix', 'features', 'flops', 'params', 'model_type', 'latency'])

In [6]:
import os 
import torch 
import pickle 
import numpy as np
import pandas as pd 

y = np.array(data['latency'])
y

array([2.06137 , 1.24849 , 3.32131 , ..., 0.508545, 0.390137, 0.387939],
      shape=(20000,))

In [7]:
from scipy import stats
stats.describe(y)

DescribeResult(nobs=20000, minmax=(0.231812, 61.5335), mean=7.88606881825, variance=48.202280883930726, skewness=1.5008993766123067, kurtosis=2.9399936878469104)